In [ ]:
# ..... metacells from hicat ..... #

In [9]:
library(Seurat)
library(scrattch.hicat)
library(dendextend)
library(dplyr)
library(matrixStats)
library(Matrix)

In [84]:
seurat_obj = readRDS('stage28_integrated_cca.rds')
df1 = read.delim('stage28_metacell.csv', sep = ',')
seurat_obj$metacell<- df1$metacell[match(rownames(seurat_obj@meta.data), df1$barcode)]
Idents(seurat_obj) <- 'metacell'

# remove outlier cells identified by metacell pipeline
seurat_obj <- seurat_obj[,!is.na(seurat_obj$metacell)]

In [85]:
DefaultAssay(seurat_obj) <- 'SCT'
seurat_obj

An object of class Seurat 
35034 features across 28971 samples within 3 assays 
Active assay: SCT (15027 features, 0 variable features)
 2 other assays present: RNA, integrated
 2 dimensional reductions calculated: pca, umap

In [89]:
seurat_obj <- PrepSCTFindMarkers(seurat_obj)

Found 3 SCT models. Recorrecting SCT counts using minimum median counts: 1870



In [88]:
dim(combos)[2]*0.7
dim(combos)[2]*0.85

[1] 34839

[1] 42304.5

In [90]:
# find all markers distinguishing each pair of metacells
options(warn = -1)
mcells = levels(seurat_obj)
combos = combn(mcells, 2)
mergedf = data.frame(cell1 = unlist(combos[1,]), cell2 = unlist(combos[2,]), merge = 0)
pb = txtProgressBar(min = 0, max = dim(combos)[2], initial = 0)

for(ii in 42306:dim(combos)[2]){
    mc1 = combos[1,ii]
    mc2 = combos[2,ii]
    cluster.markers <- FindMarkers(seurat_obj, ident.1 = mc1, ident.2 = mc2, 
                                logfc.threshold = 1, min.pct = 0.5, 
                                min.diff.pct = 0.3, recorrect_umi = FALSE)
    mrk = dim(cluster.markers)[1]
    if(mrk<5){
        mergedf$merge[ii] = 1
    }
    setTxtProgressBar(pb, ii)
}

mergedf[1:3,]

cell1 cell2 merge
1 25    182   0    
2 25    287   0    
3 25    108   0

In [91]:
head(mergedf[mergedf$merge==1,])

cell1 cell2 merge
42522 147   102   1    
42543 147   124   1    
42546 147   136   1    
42554 147   101   1    
42560 147   141   1    
42566 147   150   1

In [92]:
# save
write.table(mergedf, file = 'stage28_merge_metacell_de.csv', sep = ',', row.names = F,
           col.names = T, quote = F)

In [ ]:
tab1 = read.delim('stage28_cluster_from_metacell_de.csv', sep = ',')

In [51]:
# find all markers of cluster 2
# cluster2.markers <- FindMarkers(seurat_obj, ident.1 = 2, min.pct = 0.25, 
#                                 assay = 'SCT', recorrect_umi = FALSE)
# head(cluster2.markers, n = 5)

p_val        avg_log2FC pct.1 pct.2 p_val_adj   
VWDE     9.347500e-72 1.4754187  0.662 0.091 1.389132e-67
FAM135B  3.413788e-71 1.7394195  0.403 0.033 5.073231e-67
SORCS3   8.688232e-69 1.8038527  0.727 0.115 1.291158e-64
WDFY4    1.007486e-65 0.3738722  0.260 0.015 1.497225e-61
CRISPLD1 4.585830e-58 1.3395157  0.494 0.062 6.815002e-54